# GPS

A key failing of the previous model was the lack of measurements with external reference, leading to compounding errors in some state predictions. In the following notebook, we are going to trial integrating simulated GPS data, using the provided waypoint data. 

The following code generates the environment from a sensor config and a random test data set.

In [4]:
import re
import os
import random
from datetime import datetime

import numpy as np
from numpy.typing import NDArray


from estimators.kalman_filter import KalmanFilter
from estimators.utils import (
    filter_acceleration, generate_body_estimates, generate_euler_rates
)
from estimators.visualise import (
    plot_2d_timeseries, plot_3d_timeseries, plot_uncertainty_timeseries
)
from estimators.sensors import (
    Accelerometer,
    AccelerometerUncalibrated,
    Gyroscope,
    GyroscopeUncalibrated,
    Magnetometer,
    MagnetometerUncalibrated,
    Measurement,
    RotationVector,
    Sensor,
    Waypoint,
)


# Load environment 
data_dir = "data/indoor_robot/train/"
config_file = "sensor_config.txt"
sensor_config = data_dir + config_file

with open(sensor_config, "r", encoding="utf-8") as f:
    lines = f.readlines()
    
def create_sensor(config):
    params = {}
    # Parse config string into parameter list
    config = re.findall("([a-zA-Z]*):([a-zA-Z0-9 .]*)", config)
    for field, value in config:
        params[field] = value
    
    # Parse model name and type
    name = params.pop("name")
    id, type = name[: name.find(" ")], name[name.find(" ") + 1 :]
    params.update({"id": id, "type": type})

    # Grab sensor class from type name
    sensor = eval(type.replace(" ", ""))
    return sensor(**params)

# Load sensor config
sensors = {}

for line in lines:
    if line.find("type:") != -1:
        sensor = create_sensor(line)
        if sensor:
            sensors[sensor.type.lower()] = sensor

            
# Randomly select test data set file
files = [f for f in os.listdir(data_dir) if f != config_file]
file_path = data_dir + random.choice(files)


with open(file_path, "r", encoding="utf-8") as f:
    lines = f.readlines()

def process_measurement(reading: str):
    data = reading.rstrip("\n").split("\t")

    t = datetime.fromtimestamp(int(data[0]) / 1000.0)
    measurement = data[2:]
    
    # Convert sensor reading definition into a sensor type 
    reading_type = data[1].lstrip("TYPE_")
    sensor_type = (
        reading_type.replace("MAGNETIC_FIELD", "MAGNETOMETER").lower().replace("_", " ")
    )
    return (
        t,
        sensor_type,
        measurement,
    )
    
waypoints = {}
time_ = set()

for line in lines:
    if line.startswith("#"):
        continue
    else:
        t, sensor_type, measurement = process_measurement(line)
        if sensor_type == "waypoint":
            waypoints[t] = Waypoint(t, *measurement)
        elif sensor := sensors.get(sensor_type):
            sensor.add_reading(t, *measurement)
        time_.add(t)

time_ = sorted(list(time_))

start_t = time_[0]
end_t = time_[-1]
print(f"{len(time_)} sensor readings collected between {start_t} and {end_t}")

11885 sensor readings collected between 2019-10-19 23:10:31.054000 and 2019-10-19 23:14:21.045000


The provided waypoints for this data set can be seen below.

In [5]:
# Plot 3D position over time
x_way = np.array([waypoint.x for waypoint in waypoints.values()])
y_way = np.array([waypoint.y for waypoint in waypoints.values()])
z_way = np.array([waypoint.z for waypoint in waypoints.values()])
plot_3d_timeseries(
    time_,
    x=[],
    y=[],
    z=[],
    x_true=x_way,
    y_true=y_way,
    z_true=z_way,
    title="Path waypoints",
    scene=dict(zaxis=dict(range=[-10, 10])),
)

## Position Interpolation

There are clearly more waypoints than measurements, so we will have to interpolate the values to generate enough sample data. For this, we will try a range of interpolation methods to get the best fit. The following code uses linear, quadratic, and cubic interpolation to estimate the position of the robot at each measurement timestep.

In [6]:
import numpy as np
from scipy.interpolate import interp1d

waypoint_range = [(t - start_t).total_seconds() for t in list(waypoints.keys())]
measurement_range = [(t - start_t).total_seconds() for t in time_ if t < list(waypoints.keys())[-1]]


for interp_type in ["linear", "quadratic", "cubic"]:
    x_interp = interp1d(waypoint_range, x_way, kind=interp_type)
    y_interp = interp1d(waypoint_range, y_way, kind=interp_type)
    z_interp = interp1d(waypoint_range, z_way, kind=interp_type)

    x_est = x_interp(measurement_range)
    y_est = y_interp(measurement_range)
    z_est = z_interp(measurement_range)

    plot_3d_timeseries(
        time_,
        x=x_est,
        y=y_est,
        z=z_est,
        x_true=x_way,
        y_true=y_way,
        z_true=z_way,
        title=f"Position estimate using {interp_type} interpolation",
        scene=dict(zaxis=dict(range=[-10, 10])),
    )


Of the three, linear interpolation provides the most direct path between the waypoints. However quadratic and cubic follow a more natural path of a robot, so we will use them as our estimate. Both display similar trajectories so we will use quadratic. 

The waypoints represent the true position of the data, so to simulate read GPS data, we'll need to add noise to the data. GPS-enabled smartphones are accurate to within a 4.9m radius [[1](https://www.gps.gov/systems/gps/performance/accuracy/)], so we will use this as an inital noise estimate.

In [7]:
x_interp = interp1d(waypoint_range, x_way, kind="quadratic")
y_interp = interp1d(waypoint_range, y_way, kind="quadratic")
z_interp = interp1d(waypoint_range, z_way, kind="quadratic")

x_est = x_interp(measurement_range)
y_est = y_interp(measurement_range)
z_est = z_interp(measurement_range)

error = 4.9
x_noisy = x_est + np.random.normal(0, np.sqrt(error), x_est.shape[0])
y_noisy = y_est + np.random.normal(0, np.sqrt(error), y_est.shape[0])
z_noisy = z_est + np.random.normal(0, np.sqrt(error), z_est.shape[0])

plot_3d_timeseries(
    time_,
    x=x_noisy,
    y=y_noisy,
    z=z_noisy,
    x_true=x_est,
    y_true=y_est,
    z_true=z_est,
    title=f"Noisy GPS position compared with true position",
    scene=dict(zaxis=dict(range=[-10, 10])),
)

We can see that the "measured" positions are much less refined and display significant noise, similar to the kind of data we'd expect from a real GPS-enabled smart-phone. From here, we can build our GPS sensor and integrate the readings into a kalman filter.